In [10]:
#The code that inputs all videos and creates a CSV file of position of the hand

import cv2 as cv
import matplotlib.pyplot as plt
import csv
from csv import writer

net = cv.dnn.readNetFromTensorflow("graph_opt.pb")

inWidth = 368
inHeight = 368
inScale = 1

thr = 0.2

BODY_PARTS = {"Nose": 0, "Neck": 1, "RShoulder": 2, "RElbow": 3, "RWrist": 4,
              "LShoulder": 5, "LElbow": 6, "LWrist": 7, "RHip": 8, "RKnee": 9,
              "RAnkle": 10, "LHip": 11, "LKnee": 12, "LAnkle": 13, "REye": 14,
              "LEye": 15, "REar": 16, "LEar": 17, "Background": 18}

POSE_PAIRS = [["Neck", "RShoulder"], ["Neck", "LShoulder"], ["RShoulder", "RElbow"],
              ["RElbow", "RWrist"], ["LShoulder", "LElbow"], ["LElbow", "LWrist"],
              ["Neck", "RHip"], ["RHip", "RKnee"], ["RKnee", "RAnkle"], ["Neck", "LHip"],
              ["LHip", "LKnee"], ["LKnee", "LAnkle"], ["Neck", "Nose"], ["Nose", "REye"],
              ["REye", "REar"], ["Nose", "LEye"], ["LEye", "LEar"]]

#Import image

#img = cv.imread("pose.png")
#plt.imshow(img)
#plt.imshow(cv.cvtColor(img, cv.COLOR_BGR2RGB))


def pose_estimation(frame):
    frameWidth = frame.shape[1]
    frameHeight = frame.shape[0]
    inp = cv.dnn.blobFromImage(frame, inScale, (inWidth, inHeight),
                               (0, 0, 0), swapRB=False, crop=False)
    net.setInput(inp)
    out = net.forward()

    assert (len(BODY_PARTS) <= out.shape[1])

    points = []
    for i in range(len(BODY_PARTS)):
        # Slice heatmap of corresponding body's part.
        heatMap = out[0, i, :, :]

        # Originally, we try to find all the local maximums. To simplify a sample
        # we just find a global one. However only a single pose at the same time
        # could be detected this way.
        _, conf, _, point = cv.minMaxLoc(heatMap)
        x = (frameWidth * point[0]) / out.shape[3]
        y = (frameHeight * point[1]) / out.shape[2]

        # Add a point if it's confidence is higher than threshold.
        points.append((int(x), int(y)) if conf > thr else None)

    for pair in POSE_PAIRS:
        partFrom = pair[0]
        partTo = pair[1]
        assert (partFrom in BODY_PARTS)
        assert (partTo in BODY_PARTS)

        idFrom = BODY_PARTS[partFrom]
        idTo = BODY_PARTS[partTo]

        if points[idFrom] and points[idTo]:
            cv.line(frame, points[idFrom], points[idTo], (0, 255, 0), 3)
            cv.ellipse(frame, points[idFrom], (3, 3), 0, 0, 360, (0, 0, 255), cv.FILLED)
            cv.ellipse(frame, points[idTo], (3, 3), 0, 0, 360, (0, 0, 255), cv.FILLED)

    t, _ = net.getPerfProfile()
    freq = cv.getTickFrequency() / 1000
    cv.putText(frame, '%.2fms' % (t / freq), (10, 20), cv.FONT_HERSHEY_SIMPLEX, 0.5, (0, 0, 0))
    return frame



#estimated_image = pose_estimation(img)
#plt.imshow(cv.cvtColor(estimated_image, cv.COLOR_BGR2RGB))

#Video
vidcoordinates = []

vidvalue = []
vidnames=[]
namessubjects = ['Andrei','Elsa','Nathalie','Oskar','Viktor']
for i in range(4):
    for j in namessubjects:
        for k in range(10):
            if k != 9 and (i != 1 and j != 'Andrei' or i != 2 and j != 'Natalie'):
                    vidvalue.append(i)
                    vidnames.append(f'Armpares {i} - {j} - {k+1}.mp4')
#vidnamess = ['Pares i arm right 3 - 1080 50fps - 1_Trim.mp4', 'Pares i arm right 3 - 1080 50fps - 2_Trim.mp4']
#vidnamess = ['nataliepeka1_1_20.mp4', 'nataliepeka1_4_20.mp4']
for i in vidnames:
    print(i)
    allpointsright =[]
    allpointsleft = []
    allpoints = []
    cap = cv.VideoCapture(i)
    cap.set(3, 800)
    cap.set(4, 800)

    if not cap.isOpened():
        cap = cv.VideoCapture(0)
    if not cap.isOpened():
        raise IOError('Cannot open video')
    while cv.waitKey(1) < 0:
        hasFrame, frame = cap.read()
        if not hasFrame:
            cv.waitKey()
            break
        frameWidth = frame.shape[1]
        frameHeight = frame.shape[0]
        inp = cv.dnn.blobFromImage(frame, inScale, (inWidth, inHeight),
                                   (0, 0, 0), swapRB=False, crop=False)
        net.setInput(inp)
        out = net.forward()

        assert (len(BODY_PARTS) <= out.shape[1])

        points = []
        for i in range(len(BODY_PARTS)):
            # Slice heatmap of corresponding body's part.
            heatMap = out[0, i, :, :]

            # Originally, we try to find all the local maximums. To simplify a sample
            # we just find a global one. However only a single pose at the same time
            # could be detected this way.
            _, conf, _, point = cv.minMaxLoc(heatMap)
            x = (frameWidth * point[0]) / out.shape[3]
            y = (frameHeight * point[1]) / out.shape[2]

            # Add a point if it's confidence is higher than threshold.
            points.append((int(x), int(y)) if conf > thr else None)

        for pair in POSE_PAIRS:
            partFrom = pair[0]
            partTo = pair[1]
            assert (partFrom in BODY_PARTS)
            assert (partTo in BODY_PARTS)

            idFrom = BODY_PARTS[partFrom]
            idTo = BODY_PARTS[partTo]

            if points[idFrom] and points[idTo]:
                cv.line(frame, points[idFrom], points[idTo], (0, 255, 0), 3)
                cv.ellipse(frame, points[idFrom], (3, 3), 0, 0, 360, (0, 0, 255), cv.FILLED)
                cv.ellipse(frame, points[idTo], (3, 3), 0, 0, 360, (0, 0, 255), cv.FILLED)

        t, _ = net.getPerfProfile()
        freq = cv.getTickFrequency() / 2000
        cv.putText(frame, '%.2fms' % (t / freq), (10, 20), cv.FONT_HERSHEY_SIMPLEX, 0.5, (0, 0, 0))
        #print(points)
        #cv.imshow('Pose estimation Tutorial', frame)
        
        if points[4] is not None:
            allpointsright.append(points[4][1]/1080)
        if points[7] is not None:
            allpointsleft.append(points[7][1]/1080)
    if min(allpointsright) < min(allpointsleft):
        #vidcoordinates.append(allpointsright)
        with open('vidcoordinates.csv', 'a') as f_object:
            writer_object = writer(f_object)
            writer_object.writerow(allpointsright)
            f_object.close()
        print('right')
        #print(allpointsright)
    elif min(allpointsright) > min(allpointsleft):
        #vidcoordinates.append(allpointsleft)
        with open('vidcoordinates.csv', 'a') as f_object:
            writer_object = writer(f_object)
            writer_object.writerow(allpointsleft)
            f_object.close()
        print('left')
        #print(allpointsleft)
    
#print(vidcoordinates)


input_variable=[]
for i in range(5):
    input_variable.append(vidcoordinates[i])

with open ('coordinates_data.csv','w',newline = '') as csvfile:
    my_writer = csv.writer(csvfile, delimiter = ' ')
    my_writer.writerows(input_variable)

Armpares 0 - Andrei - 1.mp4
left
Armpares 0 - Andrei - 2.mp4
right
Armpares 0 - Andrei - 3.mp4
right
Armpares 0 - Andrei - 4.mp4
right
Armpares 0 - Andrei - 5.mp4
right
Armpares 0 - Andrei - 6.mp4
right
Armpares 0 - Andrei - 7.mp4
left
Armpares 0 - Andrei - 8.mp4
left
Armpares 0 - Andrei - 9.mp4
left
Armpares 0 - Elsa - 1.mp4
left
Armpares 0 - Elsa - 2.mp4
right
Armpares 0 - Elsa - 3.mp4
right
Armpares 0 - Elsa - 4.mp4
right
Armpares 0 - Elsa - 5.mp4
right
Armpares 0 - Elsa - 6.mp4
right
Armpares 0 - Elsa - 7.mp4
left
Armpares 0 - Elsa - 8.mp4
left
Armpares 0 - Elsa - 9.mp4
left
Armpares 0 - Nathalie - 1.mp4
right
Armpares 0 - Nathalie - 2.mp4
right
Armpares 0 - Nathalie - 3.mp4
right
Armpares 0 - Nathalie - 4.mp4
right
Armpares 0 - Nathalie - 5.mp4
right
Armpares 0 - Nathalie - 6.mp4
left
Armpares 0 - Nathalie - 7.mp4
left
Armpares 0 - Nathalie - 8.mp4
left
Armpares 0 - Nathalie - 9.mp4
left
Armpares 0 - Oskar - 1.mp4
left
Armpares 0 - Oskar - 2.mp4
right
Armpares 0 - Oskar - 3.mp4
ri

IndexError: list index out of range

In [11]:
#From csv to list
#Börja med att köra denna när du har 'vidcoordinates.csv' i samma mapp som denna fil

import csv
import cv2 as cv
import matplotlib.pyplot as plt
import csv
from csv import writer

with open('vidcoordinates.csv', newline='') as f:
    reader = csv.reader(f)
    data = list(reader)

newbetterlist = []
for i in data:
    if i:
        newbetterlist.append(i)
print(newbetterlist)

[['0.5', '0.5', '0.5', '0.5', '0.5', '0.5', '0.5', '0.5', '0.5', '0.5', '0.5', '0.5', '0.5', '0.5', '0.4777777777777778', '0.4777777777777778', '0.4777777777777778', '0.4777777777777778', '0.4777777777777778', '0.4777777777777778', '0.4564814814814815', '0.4564814814814815', '0.43425925925925923', '0.43425925925925923', '0.43425925925925923', '0.43425925925925923', '0.412962962962963', '0.412962962962963', '0.3907407407407407', '0.3907407407407407', '0.3907407407407407', '0.36944444444444446', '0.3472222222222222', '0.3472222222222222', '0.3472222222222222', '0.32592592592592595', '0.32592592592592595', '0.3037037037037037', '0.3037037037037037', '0.3037037037037037', '0.3037037037037037', '0.3037037037037037', '0.3037037037037037', '0.3037037037037037', '0.3037037037037037', '0.3037037037037037', '0.2824074074074074', '0.2824074074074074', '0.2824074074074074', '0.2601851851851852', '0.2601851851851852', '0.2601851851851852', '0.2601851851851852', '0.2601851851851852', '0.260185185185

In [12]:
vidcoordinates = newbetterlist

In [25]:
#Make strings into ints

for i in range(len(vidcoordinates)):
    for j in range(len(vidcoordinates[i])):
        vidcoordinates[i][j] = float(vidcoordinates[i][j])
print(vidcoordinates)

[[0.5, 0.5, 0.5, 0.5, 0.5, 0.5, 0.5, 0.5, 0.5, 0.5, 0.5, 0.5, 0.5, 0.5, 0.4777777777777778, 0.4777777777777778, 0.4777777777777778, 0.4777777777777778, 0.4777777777777778, 0.4777777777777778, 0.4564814814814815, 0.4564814814814815, 0.43425925925925923, 0.43425925925925923, 0.43425925925925923, 0.43425925925925923, 0.412962962962963, 0.412962962962963, 0.3907407407407407, 0.3907407407407407, 0.3907407407407407, 0.36944444444444446, 0.3472222222222222, 0.3472222222222222, 0.3472222222222222, 0.32592592592592595, 0.32592592592592595, 0.3037037037037037, 0.3037037037037037, 0.3037037037037037, 0.3037037037037037, 0.3037037037037037, 0.3037037037037037, 0.3037037037037037, 0.3037037037037037, 0.3037037037037037, 0.2824074074074074, 0.2824074074074074, 0.2824074074074074, 0.2601851851851852, 0.2601851851851852, 0.2601851851851852, 0.2601851851851852, 0.2601851851851852, 0.2601851851851852, 0.2601851851851852, 0.2601851851851852, 0.2601851851851852, 0.2388888888888889, 0.2388888888888889, 0.2

In [13]:
#Append zeros to make the same size
lengths = []
for i in vidcoordinates:
    lengths.append(len(i))
print(lengths)
print(max(lengths))

for i in vidcoordinates:
    while len(i) < max(lengths):
        i.append(0)
print(vidcoordinates)

[523, 525, 551, 545, 492, 465, 517, 524, 524, 419, 534, 531, 504, 512, 540, 489, 504, 465, 506, 495, 515, 531, 502, 460, 148, 178, 162, 564, 569, 609, 615, 572, 572, 562, 563, 565, 524, 532, 504, 511, 511, 491, 555, 529, 585, 518, 543, 568, 557, 556, 608, 543, 527, 539, 501, 523, 530, 481, 530, 513, 470, 536, 534, 502, 585, 500, 506, 513, 524, 496, 474, 521, 559, 614, 623, 551, 570, 637, 554, 551, 582, 562, 588, 575, 566, 565, 567, 586, 558, 561, 594, 558, 594, 595, 569, 612, 564, 573, 557, 509, 515, 520, 511, 511, 519, 523, 542, 500, 554, 607, 567, 524, 611, 546, 601, 573, 566, 553, 579, 576, 578, 547, 557, 564, 549, 560, 393, 374, 531, 381, 459, 505, 459, 398, 479, 407, 337, 322, 346, 370, 399, 374, 380, 410, 282, 312, 312, 276, 280, 284, 270, 295, 337, 466, 371, 407, 424, 405, 435, 491, 413, 383, 314, 349, 312, 285, 277, 273, 301, 291, 323]
637
[['0.5', '0.5', '0.5', '0.5', '0.5', '0.5', '0.5', '0.5', '0.5', '0.5', '0.5', '0.5', '0.5', '0.5', '0.4777777777777778', '0.477777777777777

In [26]:
#Denna cell är själva neurala nätverket, så lägg in en till cell under som tar samma input men med annan ML-algoritm

from sklearn.model_selection import train_test_split
from matplotlib import pyplot as plt
from tensorflow.keras import datasets, layers, models
import tensorflow as tf

import numpy as np

y = np.array(vidvalue)
X = np.array(vidcoordinates)



X_train, X_test, y_train, y_test = train_test_split(
    X, y, test_size=0.25, random_state=42)
#X_train, X_test = X_train / 1080.0, X_test / 1080.0
print(X_train)
print(y_train)
#Gammalt

X_train = tf.convert_to_tensor(X_train, dtype=tf.float32)
y_train = tf.convert_to_tensor(y_train, dtype=tf.float32)

model = tf.keras.models.Sequential([
  #tf.keras.layers.Flatten(input_shape=(28, 28)),
  tf.keras.layers.Dense(128, activation='relu'),
  tf.keras.layers.Dropout(0.1),
  tf.keras.layers.Dense(10, activation='softmax')
])

model.compile(optimizer='adam',
              loss='sparse_categorical_crossentropy',
              #loss=tf.keras.losses.BinaryCrossentropy(from_logits=True),
              metrics=['accuracy'])
fit_info = model.fit(X_train, y_train,
           batch_size=25,
           epochs=5,
           verbose=1,
           validation_data=(X_test, y_test))

model.fit(X_train, y_train, epochs=5)
model.evaluate(X_test, y_test)

[[0.5       0.5212963 0.5212963 ... 0.        0.        0.       ]
 [0.5212963 0.5212963 0.5212963 ... 0.        0.        0.       ]
 [0.5       0.5       0.5       ... 0.        0.        0.       ]
 ...
 [0.5       0.5       0.5212963 ... 0.        0.        0.       ]
 [0.5212963 0.5212963 0.5212963 ... 0.        0.        0.       ]
 [0.5212963 0.5       0.5       ... 0.        0.        0.       ]]
[3 0 3 3 3 1 0 1 0 2 1 2 0 1 2 0 0 1 3 0 0 0 0 1 3 2 0 3 2 0 3 2 1 0 2 0 0
 3 0 0 3 1 1 1 0 2 1 2 3 3 1 2 3 1 1 0 2 3 3 1 3 3 2 2 1 0 2 0 3 1 0 1 1 0
 1 0 0 1 3 2 2 1 3 3 1 0 0 1 3 3 0 1 3 3 3 3 1 1 2 1 3 1 1 1 0 1 3 3 0 3 0
 1 3 3 3 2 2 2 1 1 2 3 0 1 2 0 2 2]
Epoch 1/5
6/6 [==============================] - 1s 39ms/step - loss: 1.9460 - accuracy: 0.3438 - val_loss: 1.2157 - val_accuracy: 0.6512
Epoch 2/5
6/6 [==============================] - 0s 12ms/step - loss: 1.1342 - accuracy: 0.5469 - val_loss: 0.9128 - val_accuracy: 0.7209
Epoch 3/5
6/6 [==============================] - 0s 12m

[0.5747445821762085, 0.7441860437393188]

In [1]:
plt.plot(fit_info.history["accuracy"])
plt.title('Training accuracy for the Epochs')
plt.xlabel('Epochs')
plt.ylabel('Training accuracy')

plt.show()

NameError: name 'plt' is not defined

['Armpares 0 - Andrei - 1.mp4', 'Armpares 0 - Andrei - 2.mp4', 'Armpares 0 - Andrei - 3.mp4', 'Armpares 0 - Andrei - 4.mp4', 'Armpares 0 - Andrei - 5.mp4', 'Armpares 0 - Andrei - 6.mp4', 'Armpares 0 - Andrei - 7.mp4', 'Armpares 0 - Andrei - 8.mp4', 'Armpares 0 - Andrei - 9.mp4', 'Armpares 0 - Andrei - 10.mp4', 'Armpares 0 - Elsa - 1.mp4', 'Armpares 0 - Elsa - 2.mp4', 'Armpares 0 - Elsa - 3.mp4', 'Armpares 0 - Elsa - 4.mp4', 'Armpares 0 - Elsa - 5.mp4', 'Armpares 0 - Elsa - 6.mp4', 'Armpares 0 - Elsa - 7.mp4', 'Armpares 0 - Elsa - 8.mp4', 'Armpares 0 - Elsa - 9.mp4', 'Armpares 0 - Elsa - 10.mp4', 'Armpares 0 - Nathalie - 1.mp4', 'Armpares 0 - Nathalie - 2.mp4', 'Armpares 0 - Nathalie - 3.mp4', 'Armpares 0 - Nathalie - 4.mp4', 'Armpares 0 - Nathalie - 5.mp4', 'Armpares 0 - Nathalie - 6.mp4', 'Armpares 0 - Nathalie - 7.mp4', 'Armpares 0 - Nathalie - 8.mp4', 'Armpares 0 - Nathalie - 9.mp4', 'Armpares 0 - Nathalie - 10.mp4', 'Armpares 0 - Oskar - 1.mp4', 'Armpares 0 - Oskar - 2.mp4', 'Armpa